### Tqdm库的使用

#### 配合Pandas库、Numpy库食用最佳

In [1]:
# 导入tqdm库 如果没有请使用pip install tqdm 或者 conda install tqdm
from tqdm import trange
# 导入numpy库 如果没有请使用pip install numpy 或者 conda install numpy
import numpy as np
# 导入csv库
import csv

#### 函数部分

In [2]:
def sigmoid(x):
    return 1.0 / (1.0 + np.exp(-x))

def sigmoid_derivative(x):
    return sigmoid(x) * (1 - sigmoid(x))

class Net:

    def __init__(self, layers):
        self.active = sigmoid  # 激活函数
        self.active_d = sigmoid_derivative  # 激活函数的求导
        self.weights = []  # 权值参数
        self.bias = []  # 阈值参数
        for i in range(1, len(layers)):  # 参数初始化
            self.weights.append(np.random.randn(layers[i - 1], layers[i]))
            self.bias.append(np.random.randn(layers[i]))

    def core(self, x, label, learning_rate):
        y = [x]  # 保存每层激活后的输出值
        # 正向传播
        for i in range(len(self.weights)):
            y.append(self.active(np.dot(y[-1], self.weights[i]) + self.bias[i]))

        # 反向传播
        e = y[-1] - label
        deltas = [e * y[-1] * (1 - y[-1])]  # 输出层Delta值
        # 各隐藏层Delta值
        for i in range(1, len(self.weights)):
            deltas.append(np.dot(deltas[-1], self.weights[-i].T) * y[-i - 1] * (1 - y[-i - 1]))
        # 误差项倒置
        deltas.reverse()
        # 更新参数w和b
        for i in range(len(self.weights)):
            y_2d = np.atleast_2d(y[i])
            deltas_2d = np.atleast_2d(deltas[i])
            self.weights[i] -= learning_rate * np.dot(y_2d.T, deltas_2d)
            self.bias[i] -= learning_rate * deltas[i]

    def predict(self, x):
        # 正向传播预测输出值
        y = x
        for i in range(len(self.weights)):
            y = self.active(np.dot(y, self.weights[i]) + self.bias[i])
        _ = [str(round((i / y.sum()) * 100, 2)) + "%" for i in y]  # 将输出结果以概率的形式展现
        out = list(y)
        result = out.index(max(out))
        return result, _

#### 主函数部分

In [3]:
if __name__ == '__main__':

    Net = Net([784, 50, 50, 10])

    # 读取数据
    file_name = "data/train.csv"  # 数据集为42000张带标签的28x28手写数字图像
    x_train = []  # 训练集样本数据特征
    y_train = []  # 训练集样本标签
    '''
        测试集用来测试模型质量必不可少。
        验证集用来调节超参数，如神经网络层数，各层神经节点数、学习率等人为设置而不是模型通过学习得到的参数，可省略，仅用训练集即可
    '''
    x_test = []  # 测试集样本数据特征
    y_test = []  # 测试集样本标签
    with open(file_name, 'r') as f:
        reader = csv.reader(f)
        header_row = next(reader)
        for row in reader:
            data = np.array(row[1:], dtype=float)
            if np.random.random() < 0.5:  # 划分数据集 训练集：测试集 ≈ 1:1
                x_train.append(data / ((data ** 2).sum() ** 0.5))  # 每个样本对应的784个特征数值归一化
                y_train.append(int(row[0]))
            else:
                x_test.append(data / ((data ** 2).sum() ** 0.5))
                y_test.append(int(row[0]))

    print("训练样本数：{}，测试样本数：{}".format(len(y_train), len(y_test)))

    # 训练
    learning_rate = 0.5  # 初始学习率
    epochs = 5  # 训练轮数
    for i in trange(len(y_train) * epochs):
        if (i + 1) % len(y_test) == 0:
            learning_rate *= 0.5  # 每训练一轮 学习率减半
        label = np.zeros(10)
        label[y_train[i % len(y_train)]] = 1  # 设置label
        Net.core(x_train[i % len(y_train)], label, learning_rate)  # 更新网络参数

    # 预测
    count = 0
    for i in trange(len(y_test)):
        print("-------第{}个测试样本-----------".format(i + 1))
        predict, _ = Net.predict(x_test[i])
        print("概率分布:{}".format(_))
        print("预测值：{}，真实值：{}".format(predict, y_test[i]))
        if predict == y_test[i]:
            count += 1
    print("正确率：{}".format(count / len(y_test)))

训练样本数：20813，测试样本数：21187


  2%|█▎                                                                          | 350/21187 [00:00<00:06, 3452.49it/s]

-------第1个测试样本-----------
概率分布:['0.0%', '92.93%', '0.51%', '0.92%', '0.0%', '4.63%', '0.0%', '0.05%', '0.94%', '0.01%']
预测值：1，真实值：1
-------第2个测试样本-----------
概率分布:['96.81%', '0.0%', '2.64%', '0.08%', '0.0%', '0.19%', '0.0%', '0.13%', '0.04%', '0.11%']
预测值：0，真实值：0
-------第3个测试样本-----------
概率分布:['0.11%', '0.0%', '0.18%', '94.25%', '0.0%', '0.45%', '0.0%', '2.97%', '0.09%', '1.93%']
预测值：3，真实值：3
-------第4个测试样本-----------
概率分布:['0.06%', '0.0%', '0.0%', '1.13%', '0.31%', '97.02%', '0.02%', '0.0%', '1.15%', '0.3%']
预测值：5，真实值：5
-------第5个测试样本-----------
概率分布:['0.07%', '0.04%', '0.68%', '98.92%', '0.0%', '0.17%', '0.01%', '0.06%', '0.04%', '0.0%']
预测值：3，真实值：3
-------第6个测试样本-----------
概率分布:['0.0%', '0.01%', '0.01%', '0.04%', '1.24%', '0.28%', '0.0%', '1.38%', '0.86%', '96.17%']
预测值：9，真实值：9
-------第7个测试样本-----------
概率分布:['0.1%', '0.02%', '0.76%', '98.56%', '0.0%', '0.05%', '0.0%', '0.03%', '0.47%', '0.01%']
预测值：3，真实值：3
-------第8个测试样本-----------
概率分布:['0.0%', '0.0%', '0.35%', '0.09%', '0.0%', '

  6%|████▋                                                                      | 1335/21187 [00:00<00:08, 2460.13it/s]

概率分布:['0.0%', '8.06%', '91.26%', '0.34%', '0.0%', '0.02%', '0.3%', '0.0%', '0.03%', '0.0%']
预测值：2，真实值：2
-------第686个测试样本-----------
概率分布:['0.0%', '0.0%', '99.87%', '0.0%', '0.0%', '0.0%', '0.1%', '0.0%', '0.02%', '0.0%']
预测值：2，真实值：2
-------第687个测试样本-----------
概率分布:['0.14%', '0.01%', '0.16%', '50.3%', '0.05%', '0.84%', '0.0%', '0.16%', '48.01%', '0.33%']
预测值：3，真实值：8
-------第688个测试样本-----------
概率分布:['0.0%', '0.06%', '0.28%', '0.02%', '0.48%', '0.84%', '0.0%', '0.01%', '98.06%', '0.25%']
预测值：8，真实值：8
-------第689个测试样本-----------
概率分布:['0.0%', '92.82%', '1.94%', '4.57%', '0.0%', '0.1%', '0.02%', '0.01%', '0.52%', '0.01%']
预测值：1，真实值：1
-------第690个测试样本-----------
概率分布:['96.21%', '0.0%', '2.14%', '0.75%', '0.0%', '0.52%', '0.0%', '0.13%', '0.09%', '0.16%']
预测值：0，真实值：0
-------第691个测试样本-----------
概率分布:['0.0%', '98.53%', '0.09%', '0.48%', '0.0%', '0.07%', '0.01%', '0.77%', '0.02%', '0.03%']
预测值：1，真实值：1
-------第692个测试样本-----------
概率分布:['0.0%', '88.73%', '0.13%', '10.16%', '0.0%', '0.07%', '0.01

...

概率分布:['0.01%', '0.01%', '0.44%', '0.0%', '0.43%', '0.1%', '98.93%', '0.0%', '0.08%', '0.01%']
预测值：6，真实值：6
-------第19880个测试样本-----------
概率分布:['0.0%', '0.0%', '0.02%', '0.04%', '1.67%', '0.21%', '0.0%', '0.57%', '0.22%', '97.26%']
预测值：9，真实值：9
-------第19881个测试样本-----------
概率分布:['0.0%', '98.7%', '0.04%', '0.29%', '0.0%', '0.03%', '0.03%', '0.82%', '0.02%', '0.07%']
预测值：1，真实值：1
-------第19882个测试样本-----------
概率分布:['0.0%', '0.0%', '0.0%', '0.52%', '2.43%', '0.84%', '0.0%', '1.8%', '0.13%', '94.28%']
预测值：9，真实值：9
-------第19883个测试样本-----------
概率分布:['0.0%', '0.01%', '0.03%', '0.01%', '5.86%', '0.1%', '0.0%', '0.78%', '0.88%', '92.35%']
预测值：9，真实值：9
-------第19884个测试样本-----------
概率分布:['0.03%', '0.11%', '0.1%', '98.01%', '0.0%', '0.22%', '0.0%', '0.53%', '0.82%', '0.18%']
预测值：3，真实值：3
-------第19885个测试样本-----------
概率分布:['0.0%', '0.0%', '0.0%', '0.0%', '98.98%', '0.4%', '0.03%', '0.04%', '0.02%', '0.53%']
预测值：4，真实值：4
-------第19886个测试样本-----------
概率分布:['0.0%', '0.0%', '0.0%', '0.11%', '86.39%', '0.

 99%|█████████████████████████████████████████████████████████████████████████▍| 21022/21187 [00:06<00:00, 3291.59it/s]

概率分布:['0.01%', '0.0%', '0.0%', '0.03%', '0.94%', '4.87%', '0.0%', '69.61%', '0.01%', '24.53%']
预测值：7，真实值：7
-------第20556个测试样本-----------
概率分布:['0.55%', '0.0%', '0.1%', '87.88%', '0.0%', '7.3%', '0.0%', '4.11%', '0.03%', '0.03%']
预测值：3，真实值：3
-------第20557个测试样本-----------
概率分布:['0.0%', '0.06%', '0.08%', '0.0%', '23.85%', '0.0%', '73.95%', '0.0%', '0.03%', '2.02%']
预测值：6，真实值：6
-------第20558个测试样本-----------
概率分布:['0.11%', '0.3%', '0.85%', '1.35%', '0.0%', '0.64%', '0.03%', '0.0%', '96.7%', '0.01%']
预测值：8，真实值：8
-------第20559个测试样本-----------
概率分布:['0.0%', '0.0%', '0.0%', '0.0%', '0.42%', '0.03%', '0.0%', '99.43%', '0.02%', '0.1%']
预测值：7，真实值：7
-------第20560个测试样本-----------
概率分布:['0.07%', '0.0%', '0.0%', '0.01%', '0.17%', '2.69%', '0.0%', '96.88%', '0.0%', '0.18%']
预测值：7，真实值：7
-------第20561个测试样本-----------
概率分布:['0.0%', '0.0%', '0.2%', '0.0%', '49.89%', '0.09%', '0.0%', '0.55%', '1.83%', '47.44%']
预测值：4，真实值：4
-------第20562个测试样本-----------
概率分布:['0.01%', '0.01%', '1.2%', '0.0%', '0.08%', '0.13%

100%|██████████████████████████████████████████████████████████████████████████| 21187/21187 [00:06<00:00, 3195.58it/s]

正确率：0.9191957332326427
